In [4]:
import math
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import random

from SALib.sample import saltelli
from SALib.analyze import sobol


# Use log not ln
# Label axes, also with units
# Can the indices be negative?

## Definition of the range of D

# Aquifer thickness b [m]
b = 10

# Hydraulic Conductivity from Cobuto, 1999 (adapted): 10^-4 - 10^-2 [m/s]
Kmin = 1e-04 * 86400
Kmax = 1e-02 * 86400

# Specific yield Sy from Johnson, 1967: 0.21 - 0.35 [-]
Sy_min = 0.21
Sy_max = 0.35

# Calculating D using eq. (2) from Sawyer et al., 2014
Dmin_temp = (Kmin*b)/Sy_max
Dmax_temp = (Kmax*b)/Sy_min

Dmin = math.log(Dmin_temp, 10) # lower bound for diffusivity
Dmax = math.log(Dmax_temp, 10) # upper bound for diffusivity
phi = 0 # phase

def solution(x, t, A, omega, D, phi):
  """This is the function which gives back the hydraulic head
  omega: frequency
  A: amplitude
  x: distance
  t: time"""
  sinus = math.sin(-x*math.sqrt(omega/(2*D))+ omega*t + phi)
  ret = A*math.exp(-x*math.sqrt(omega/(2*D)))*sinus
  return ret 



ModuleNotFoundError: No module named 'SALib'

In [87]:
num_of_simulations = 10000

D_vector_A = [10**((Dmax - Dmin)*random.random() + Dmin) for _ in range(num_of_simulations)]
A_vector_A = [10**(random.random() - 1) for _ in range(num_of_simulations)]
omega_vector_A = [ (math.pi - 2*math.pi/7)*random.random() + 2*math.pi/7 for _ in range(num_of_simulations)]


D_vector_B = [10**((Dmax - Dmin)*random.random() + Dmin) for _ in range(num_of_simulations)]
A_vector_B = [10**(random.random() - 1) for _ in range(num_of_simulations)]
omega_vector_B = [ (math.pi - 2*math.pi/7)*random.random() + 2*math.pi/7 for _ in range(num_of_simulations)]

In [88]:
def calculate_solution(x, t, A_vector, omega_vector, D_vector):
  y = []

  for idx in range(num_of_simulations):
    hydraulic_head = solution(x, t, A_vector[idx], omega_vector[idx], D_vector[idx], phi)
    y.append(hydraulic_head)
  
  return y

In [89]:
distances = [1, 10, 100] # given in meters
timesteps = [7, 30, 180] # given in days

for x in distances:
  for t in timesteps:
    y_A = calculate_solution(x, t, A_vector_A, omega_vector_A, D_vector_A)
    y_B = calculate_solution(x, t, A_vector_B, omega_vector_B, D_vector_B)
    y_C_1 = calculate_solution(x, t, A_vector_A, omega_vector_B, D_vector_B)
    y_C_2 = calculate_solution(x, t, A_vector_B, omega_vector_A, D_vector_B)
    y_C_3 = calculate_solution(x, t, A_vector_A, omega_vector_A, D_vector_B)

    avg = (sum(y_A)/num_of_simulations) * (sum(y_B)/num_of_simulations)
        
    # First order sensitivity indices
    S_1 = ((sum([hyd_head_A*hyd_head_B for hyd_head_A, hyd_head_B in zip(y_A, y_C_1)]) / num_of_simulations) - avg) / ((sum([hyd_head_A ** 2 for hyd_head_A in y_A]) / num_of_simulations) - avg)
    S_2 = ((sum([hyd_head_A*hyd_head_B for hyd_head_A, hyd_head_B in zip(y_A, y_C_2)]) / num_of_simulations) - avg) / ((sum([hyd_head_A ** 2 for hyd_head_A in y_A]) / num_of_simulations) - avg)
    S_3 = ((sum([hyd_head_A*hyd_head_B for hyd_head_A, hyd_head_B in zip(y_A, y_C_3)]) / num_of_simulations) - avg) / ((sum([hyd_head_A ** 2 for hyd_head_A in y_A]) / num_of_simulations) - avg)

    print('S_A='+str(S_1))
    print('S_omega='+str(S_2))
    print('S_D='+str(S_3))
    print(y_C_1)

S_A=0.007902679544223754
S_omega=0.7065480930948623
S_D=0.9995696570050321
[-0.3384272630565094, 0.12960869309087125, -0.10502211016704069, -0.01886180662112548, -0.11860997825727511, 0.015171985892042737, 0.29119172220250206, -0.09956390268635829, -0.17929826112364056, 0.8376445851921845, -0.1882888956568381, -0.6334549288875038, -0.05188872524238594, -0.10681158192339596, 0.09147964933758432, -0.07393942298318054, -0.7418559646439747, 0.797832000476843, 0.17060010361884617, -0.49010065034086725, 0.0365370262391472, -0.219300870419488, -0.8342466119537624, 0.1174495119639622, 0.5293319615761886, -0.17374489184662215, 0.41072219136777804, -0.1805014764256859, 0.09911904745339029, -0.8063948699190207, 0.0980808018230218, -0.5553701438114672, 0.26982556793739676, 0.29384681071548685, 0.47654312981648084, 0.4518981407381942, 0.7167660729256888, -0.2052638287647794, 0.028969745728036025, 0.3645496844588407, 0.22598834984126298, -0.24648594811919222, 0.5812699509246754, 0.07080491401629342,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



S_A=-0.00466846972621868
S_omega=0.683664463971612
S_D=0.9603075263271725
[-0.24259805259292624, 0.027603483301079507, 0.02447506288045513, 0.03863665572059068, -0.04329672876600611, 0.09545439199234347, -0.12076992264410756, -0.010006130031955432, -0.09289828673133353, -0.14405683879287026, 0.10175178845086838, -0.38863005961635905, -0.07240039623543823, -0.057859710816788625, 0.06932604198741647, 0.1441550805135195, -0.43002115313639, 0.773831659351734, 0.08066171750654674, 0.2580795733170475, -0.11250908483173012, -0.21633954596652266, -0.6800494751645462, 0.027805613489754962, -0.20598147342887177, 0.03828655807694445, 0.2665618936655086, -0.3240549456643735, 0.006104678169719415, -0.3026957747328922, 0.17110510985399985, -0.08262642149409759, -0.09666769729799711, 0.2873987263401284, -0.3070373449835369, -0.7128950727762358, 0.4813805601773052, 0.15862314267533897, -0.09666210753155614, 0.16549244450907943, 0.19089908750357507, -0.17666516041973312, -0.5338541169657238, -0.2226129

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



S_A=-0.0018420871298790679
S_omega=0.31261040152929026
S_D=0.4389131636639331
[0.030363800667144083, 0.006990331379430942, 0.03818697362659987, 0.0016432013406001951, 0.002302502494761466, -0.0018065684925786553, 0.004784636000583648, 0.0008352377018719791, -0.01716947398558631, 0.09779054163033188, -0.03310547207584243, 0.0344253881469065, 0.006717021410948855, 0.013203398299675321, -0.001099712196223249, 0.02404833734736986, 0.006737564541320308, 0.2041810961098603, -0.0014808660934417732, -0.09995302633244485, -0.0035576142943176355, -0.08706606617382275, 0.0348687549930855, 0.02351719948729616, -0.0018465141848139316, -0.0023305847892898914, -0.004838613629549259, 0.06931009480025795, -0.0005220322548590695, 0.14176602896773297, 0.025308841460618278, 0.008180835622914077, -0.00012931238655035048, -0.015448382397469687, 0.0006265207077603082, -0.3612718298246944, 0.44410422961318935, -0.0008899250844893894, 0.0015527846350643004, -0.06767991461080543, 0.004847686379022754, 0.0026382

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [84]:
input = {
    'num_vars': 3,
    'names': ['A', 'w', 'D'],
    'bounds': [[10**(-1) , 1],
               [(2*math.pi)/7, (2*math.pi)/2],
               [10**Dmin, 10**Dmax]],
    'dists': ['unif', 'unif', 'unif'] 
}

param_values = saltelli.sample(input, N = 2**13, calc_second_order=True)

In [85]:
def return_hydraulic_head(values, x_input, t_input):
  Y = np.zeros([values.shape[0]])
  for i,X in enumerate(values):
          Y[i] = (X[0] * math.exp(-x_input * math.sqrt(X[1] / (2*X[2])))) * (math.sin(-x_input * math.sqrt((X[1] / (2*X[2])) + ((X[1] * t_input)))))   
  return Y

In [86]:
for x in distances:
    for t in timesteps:
        
        Y = return_hydraulic_head(param_values, x_input = np.array([x]), t_input = np.array([t]))
        sobol.analyze(problem, Y, print_to_console=True)

         ST   ST_conf
A  0.290212  0.007602
w  0.868128  0.021142
D  0.000077  0.000006
         S1   S1_conf
A  0.131835  0.013716
w  0.709731  0.016576
D  0.000032  0.000197
              S2   S2_conf
(A, w)  0.158359  0.019471
(A, D)  0.000018  0.021536
(w, D)  0.000026  0.018068
         ST   ST_conf
A  0.245553  0.007907
w  0.922771  0.024024
D  0.000051  0.000004
         S1   S1_conf
A  0.077210  0.010413
w  0.754396  0.019504
D  0.000011  0.000143
              S2   S2_conf
(A, w)  0.168344  0.016838
(A, D)  0.000008  0.017666
(w, D)  0.000026  0.022353
         ST   ST_conf
A  0.182755  0.004479
w  0.999493  0.024481
D  0.000040  0.000003
         S1   S1_conf
A  0.000279  0.009945
w  0.817204  0.017579
D  0.000008  0.000147
              S2   S2_conf
(A, w)  0.182439  0.013700
(A, D)  0.000128  0.018464
(w, D)  0.000021  0.016271
         ST   ST_conf
A  0.184842  0.004576
w  0.996382  0.025905
D  0.003283  0.000250
         S1   S1_conf
A  0.003126  0.009531
w  0.811693  0.0

In [62]:
for x in [1, 10, 100]:
    for t in [7, 30, 180]:
        
        Y = evaluate(param_values, x_input = np.array([x]), t_input = np.array([t]))

        Si = sobol.analyze(problem, Y, print_to_console=True)

        # Print the first-order, second-order and total sensitivity indices
        print(Si['S1'])

TypeError: ignored